<p align="center"><img width="50%" src="https://aimodelsharecontent.s3.amazonaws.com/aimodshare_banner.jpg" /></p>

# Climate Change Satellite Image Classification Competition Model Submission Guide - keras

---
**About the Original Data:**<br>
*Data and Description accessed from [Tensorflow](https://www.tensorflow.org/datasets/catalog/bigearthnet)* <br>
The BigEarthNet is a new large-scale Sentinel-2 benchmark archive, consisting of 590,326 Sentinel-2 image patches. The image patch size on the ground is 1.2 x 1.2 km with variable image size depending on the channel resolution. This is a multi-label dataset with 43 imbalanced labels, which has been simplified to single labels with 3 categories for the purposes of this competition.

To construct the BigEarthNet, 125 Sentinel-2 tiles acquired between June 2017 and May 2018 over the 10 countries (Austria, Belgium, Finland, Ireland, Kosovo, Lithuania, Luxembourg, Portugal, Serbia, Switzerland) of Europe were initially selected. All the tiles were atmospherically corrected by the Sentinel-2 Level 2A product generation and formatting tool (sen2cor). Then, they were divided into 590,326 non-overlapping image patches. Each image patch was annotated by the multiple land-cover classes (i.e., multi-labels) that were provided from the CORINE Land Cover database of the year 2018 (CLC 2018).

Bands and pixel resolution in meters:

    B01: Coastal aerosol; 60m
    B02: Blue; 10m
    B03: Green; 10m
    B04: Red; 10m
    B05: Vegetation red edge; 20m
    B06: Vegetation red edge; 20m
    B07: Vegetation red edge; 20m
    B08: NIR; 10m
    B09: Water vapor; 60m
    B11: SWIR; 20m
    B12: SWIR; 20m
    B8A: Narrow NIR; 20m

License: Community Data License Agreement - Permissive, Version 1.0."

**Competition Data Specifics:**<br>
For the purpose of this competition, the original BigEarthNet dataset has been simplified to 20,000 images (15,000 training images and 5,000 test images) with 3 categories: "forest", "nonforest", and "snow_shadow_cloud", which contains images of snow and clouds. <br>
Each "image" is a folder with 12 satellite image layers, each of which pics up on different features. The example preprocessor uses just three layers: B02, B03, and B04, which contain the standard RGB layers used in ML models. However, you are free to use any combination of the satellite image layers. 

**Data Source:**<br>
Sumbul, G, Charfuelan, M, Demir, B and Markl, V. (2019). BigEarthNet: A Large-Scale Benchmark Archive For Remote Sensing Image Understanding. *Computing Research Repository (CoRR), abs/1902.06148.* https://www.tensorflow.org/datasets/catalog/bigearthnet




# Overview
---

Let's share our models to a centralized leaderboard, so that we can collaborate and learn from the model experimentation process...

**Instructions:**
1.   Get data in and set up X_train / X_test / y_train
2.   Preprocess data / Write and Save Preprocessor function
3. Fit model on preprocessed data and save preprocessor function and model 
4. Generate predictions from X_test data and submit model to competition
5. Repeat submission process to improve place on leaderboard



## 1. Load Data

In [1]:
!python -V

Python 3.8.0


In [2]:
#install aimodelshare library
! pip install aimodelshare-nightly

In [3]:
# Get competition data - May take a couple minutes due to size of data set
# from aimodelshare import download_data
# download_data('public.ecr.aws/y2e2a1d6/climate_competition_data-repository:latest') 

In [4]:
# # Unzip Data - May take a couple minutes due to size of data set
# import zipfile
# with zipfile.ZipFile('climate_competition_data/climate_competition_data.zip', 'r') as zip_ref:
#     zip_ref.extractall('competition_data')

##2.   Preprocess data / Write and Save Preprocessor function


In [5]:
# Set up for data preprocessing
import numpy as np
import os
import PIL
import PIL.Image
import tensorflow as tf
import tensorflow_datasets as tfds

In [35]:
# Here is a pre-designed preprocessor, but you could also build your own to prepare the data differently

def preprocessor(imageband_directory):
    """
    This function preprocesses reads in images, resizes them to a fixed shape and
    min/max transforms them before converting feature values to float32 numeric values
    required by onnx files.

    params:
        imageband_directory
            path to folder with 13 satellite image bands

    returns:
        X
            numpy array of preprocessed image data

    """

    import PIL
    import os
    import numpy as np
    import tensorflow_datasets as tfds

    def _load_tif(data):
        """Loads TIF file and returns as float32 numpy array."""
        img = tfds.core.lazy_imports.PIL_Image.open(data)
        img = np.array(img.getdata()).reshape(img.size).astype(np.float32)
        return img

    def preprocess_image(imgarray): 
        return imgarray
#         return (imgarray/np.max(imgarray))  # Preprocessing for Model-8 , Divide by max of each channel.
#         return (imgarray*255/np.max(imgarray))  # Preprocessing for Model-9 , Divide by max of each channel.

    image_list = []

    filelist1 = os.listdir(imageband_directory)

    for fpath in filelist1:
        fullpath = imageband_directory+"/"+fpath

        if fullpath.endswith(('B02.tif', 'B03.tif', 'B04.tif')):
            imgarray = _load_tif(imageband_directory+"/"+fpath)
            image_list.append(preprocess_image(imgarray))

        if fullpath.endswith('B05.tif'):
            vegetation_red_edge1 = _load_tif(imageband_directory+"/"+fpath)

        if fullpath.endswith('B06.tif'):
            vegetation_red_edge2 = _load_tif(imageband_directory+"/"+fpath)

        if fullpath.endswith('B07.tif'):
            vegetation_red_edge3 = _load_tif(imageband_directory+"/"+fpath)

        if fullpath.endswith('B11.tif'):
            SWIR_1 = _load_tif(imageband_directory+"/"+fpath)

        if fullpath.endswith('B12.tif'):
            SWIR_2 = _load_tif(imageband_directory+"/"+fpath)

        if fullpath.endswith('B8A.tif'):
            narrow_nir = _load_tif(imageband_directory+"/"+fpath)

        if fullpath.endswith('B08.tif'):
            nir = _load_tif(imageband_directory+"/"+fpath)
        
        if fullpath.endswith('B01.tif'):
            coastal = _load_tif(imageband_directory+"/"+fpath)

        if fullpath.endswith('B09.tif'):
            water = _load_tif(imageband_directory+"/"+fpath)

    mean_vegetation = (vegetation_red_edge1 + vegetation_red_edge2 + vegetation_red_edge3)/3

    mean_swir = (SWIR_1 + SWIR_2)/2

    mean_vegetation = np.repeat(np.repeat(mean_vegetation, 2, axis=1), 2, axis=0)
    
    mean_swir = np.repeat(np.repeat(mean_swir,2,axis=1),2,axis=0)

    narrow_nir = np.repeat(np.repeat(narrow_nir,2,axis=1),2,axis=0)

    mean_nir = (narrow_nir + nir)/2
        
    mean_vapour = (coastalstal + water)/2 
    
    mean_vapour = np.repeat(np.repeat(mean_vapour,6,axis=1),6,axis=0)
    image_list.append(preprocess_image(mean_vegetation))
    image_list.append(preprocess_image(mean_swir))
    image_list.append(preprocess_image(mean_nir))
    image_list.append(preprocess_image(mean_vapour))

    X = np.stack(image_list, axis=2)   # to get (height,width,3)

    # Expand dims to add "1" to object shape [1, h, w, channels] for keras model.
    X = np.expand_dims(X, axis=0)

    X = np.array(X, dtype=np.float32)  # Final shape for onnx runtime.

    return X

In [7]:
# # Create complete list of file names
# forestfilenames = ["competition_data/trainingdata/forest/" +
#                    x for x in os.listdir("competition_data/trainingdata/forest")]
# nonforestfilenames = ["competition_data/trainingdata/nonforest/" +
#                       x for x in os.listdir("competition_data/trainingdata/nonforest")]
# otherfilenames = ["competition_data/trainingdata/other/" +
#                   x for x in os.listdir("competition_data/trainingdata/other")]

# filenames = forestfilenames+nonforestfilenames+otherfilenames


# # preprocess rbg images into 120,120,3 numpy ndarray
# preprocessed_image_data = []
# for i in filenames:
#     try:
#         preprocessed_image_data.append(preprocessor(i))
#     except Exception as e:
#         print(e)
#         pass

In [8]:
model_number = 11

In [9]:
# np.save(f"6_Channel_PreProcessedImages_Model{model_number}",preprocessed_image_data)

In [10]:
preprocessed_image_data = np.load(f"6_Channel_PreProcessedImages_Model{model_number}.npy")

In [11]:
# Set up y data
from itertools import repeat
forest=repeat("forest",5000)
nonforest=repeat("nonforest",5000)
other=repeat("snow_shadow_cloud",5000)
ylist=list(forest)+list(nonforest)+list(other)

In [12]:
# Shuffle X and y data
from sklearn.utils import shuffle
X_train, y_train = shuffle(preprocessed_image_data, ylist, random_state=0)

In [13]:
X_train=np.vstack(X_train) # convert X from list to array

In [14]:
X_train.shape

(15000, 120, 120, 7)

In [15]:
X_train.shape

for i in range(7):
    print(f"Max Value of {i} channel is {X_train[:,:,:,i].max()}")

Max Value of 0 channel is 18468.0
Max Value of 1 channel is 18552.0
Max Value of 2 channel is 18581.0
Max Value of 3 channel is 16522.0
Max Value of 4 channel is 15270.0
Max Value of 5 channel is 16198.0
Max Value of 6 channel is 15411.0


In [16]:
def divide_channelbyMax(X_train):
    max_ValueArray = [] 
    for i in range(7): 
        max_ValueArray.append(X_train[:,:,:,i].max())
        X_train[:,:,:,i] = (X_train[:,:,:,i]*255)/max_ValueArray[-1]
    return X_train,max_ValueArray

In [17]:
X_train,max_ValueArray = divide_channelbyMax(X_train)

In [18]:
max_ValueArray

[18468.0, 18552.0, 18581.0, 16522.0, 15270.0, 16198.0, 15411.0]

In [19]:
X_train.shape

for i in range(7):
    print(f"Max Value of {i} channel is {X_train[:,:,:,i].max()}")

Max Value of 0 channel is 255.0
Max Value of 1 channel is 255.0
Max Value of 2 channel is 255.0
Max Value of 3 channel is 255.0
Max Value of 4 channel is 255.0
Max Value of 5 channel is 255.0
Max Value of 6 channel is 255.0


In [20]:
X_train.shape

(15000, 120, 120, 7)

##3. Fit model on preprocessed data and save preprocessor function and model 


In [21]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Activation, Dropout, BatchNormalization, Flatten
from tensorflow.keras.optimizers import SGD
from tensorflow.keras.layers import Conv2D, MaxPooling2D,GlobalAveragePooling2D
from tensorflow.keras.applications.resnet_v2 import ResNet50V2
from tensorflow.keras.applications.densenet import DenseNet121 

from tensorflow.keras.layers import RandomHeight ,RandomZoom , RandomTranslation , RandomContrast


import tensorflow as tf
import pandas 


In [22]:
# Run using GPU
with tf.device('/device:GPU:0'): # "/GPU:0": Short-hand notation for the first GPU of your machine that is visible to TensorFlow.
    
    model = Sequential()
    model.add(ResNet50V2(include_top=False , weights=None ,input_shape=(120,120,7)))
    model.add(Flatten())
    
    model.add(Dense(64, activation='relu'))
    model.add(Dropout(0.2)) 
    
    model.add(Dense(64, activation='relu')) 
    model.add(Dropout(0.2)) 

    model.add(Dense(16, activation='relu')) 
    model.add(Dropout(0.2)) 
    
    model.add(Dense(3, activation='softmax')) # Last fully-connected layer of 3 outputs (3 categories).

    model.summary()
    
    
    
    model.compile(loss='categorical_crossentropy',optimizer=tf.keras.optimizers.Adam(5e-4),
              metrics=['accuracy'])
    
    
    
    def scheduler(epoch, lr):
        if epoch < 5 :
            return lr
        else:
            return lr * tf.math.exp(-0.5)
    
    Model_Checkpoint = tf.keras.callbacks.ModelCheckpoint(f"Model{model_number}",save_best_only=True)
    
    
    Learningrate_Scheduler  = tf.keras.callbacks.LearningRateScheduler(scheduler)
    

    model.fit(  X_train, 
                pandas.get_dummies(y_train),
                validation_split = .3, 
                epochs = 10,
                callbacks=[Model_Checkpoint,Learningrate_Scheduler])
    

    model.save(f"Model{model_number}.h5")


2022-03-24 15:52:49.189317: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-03-24 15:52:49.432376: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-03-24 15:52:49.433323: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-03-24 15:52:49.438886: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 resnet50v2 (Functional)     (None, 4, 4, 2048)        23577344  
                                                                 
 flatten (Flatten)           (None, 32768)             0         
                                                                 
 dense (Dense)               (None, 64)                2097216   
                                                                 
 dropout (Dropout)           (None, 64)                0         
                                                                 
 dense_1 (Dense)             (None, 64)                4160      
                                                                 
 dropout_1 (Dropout)         (None, 64)                0         
                                                                 
 dense_2 (Dense)             (None, 16)                1

2022-03-24 15:52:54.335431: W tensorflow/core/framework/cpu_allocator_impl.cc:82] Allocation of 4233600000 exceeds 10% of free system memory.
2022-03-24 15:52:58.077855: W tensorflow/core/framework/cpu_allocator_impl.cc:82] Allocation of 4233600000 exceeds 10% of free system memory.


Epoch 1/10


2022-03-24 15:53:09.376074: I tensorflow/stream_executor/cuda/cuda_dnn.cc:384] Loaded cuDNN version 8100
2022-03-24 15:53:12.092890: W tensorflow/stream_executor/gpu/asm_compiler.cc:111] *** WARNING *** You are using ptxas 9.1.108, which is older than 11.1. ptxas before 11.1 is known to miscompile XLA code, leading to incorrect results or invalid-address errors.

You may not need to update to CUDA 11.1; cherry-picking the ptxas binary is often sufficient.


...

INFO:tensorflow:Assets written to: Model11/assets


329/329 [==============================] - 120s 364ms/step - loss: 0.4595 - accuracy: 0.8132 - val_loss: 0.4709 - val_accuracy: 0.8460 - lr: 5.0000e-04
Epoch 9/10
329/329 [==============================] - ETA: 0s - loss: 0.4662 - accuracy: 0.8107

INFO:tensorflow:Assets written to: Model11/assets


INFO:tensorflow:Assets written to: Model11/assets


329/329 [==============================] - 121s 369ms/step - loss: 0.4662 - accuracy: 0.8107 - val_loss: 0.4341 - val_accuracy: 0.8258 - lr: 5.0000e-04
Epoch 10/10
329/329 [==============================] - 93s 284ms/step - loss: 0.6050 - accuracy: 0.7636 - val_loss: 0.5362 - val_accuracy: 0.7927 - lr: 5.0000e-04


In [38]:
model.load_weights(f"Model{model_number}/")

# model.compile(loss='categorical_crossentropy',optimizer=tf.keras.optimizers.SGD(5e-7), metrics=['accuracy'])

# model.fit(  X_train, 
#                 pandas.get_dummies(y_train),
#                 validation_split = .3, 
#                 epochs = 5)
    


2022-03-24 16:25:31.101600: W tensorflow/core/util/tensor_slice_reader.cc:96] Could not open Model11/: FAILED_PRECONDITION: Model11; Is a directory: perhaps your file is in a different file format and you need to use a different restore operator?


In [24]:
print("Did it run ")


Did it run 


#### Save preprocessor function to local "preprocessor.zip" file

In [25]:
import aimodelshare as ai
ai.export_preprocessor(preprocessor,"") 

cannot pickle 'module' object
Your preprocessor is now saved to 'preprocessor.zip'


#### Save model to local ".onnx" file

In [26]:
# Save keras model to local ONNX file
from aimodelshare.aimsonnx import model_to_onnx

onnx_model = model_to_onnx(model, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("model.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString())

/home/ecbm4040/climate_change/lib/python3.8/site-packages/xgboost/compat.py:36: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  from pandas import MultiIndex, Int64Index
/usr/lib/python3.8/runpy.py:125: RuntimeWarning: 'tf2onnx.convert' found in sys.modules after import of package 'tf2onnx', but prior to execution of 'tf2onnx.convert'; this may result in unpredictable behaviour
  warn(RuntimeWarning(msg))
2022-03-24 16:12:07,058 - WARNING - '--tag' not specified for saved_model. Using --tag serve
2022-03-24 16:12:15,334 - INFO - Signatures found in model: [serving_default].
2022-03-24 16:12:15,334 - WARNING - '--signature_def' not specified, using first signature: serving_default
2022-03-24 16:12:15,335 - INFO - Output names: ['dense_3']
Instructions for updating:
Use `tf.compat.v1.graph_util.extract_sub_graph`
2022-03-24 16:12:18,424 - WARNING - From /home/ecbm4040/climate_change

## 4. Generate predictions from X_test data and submit model to competition


In [36]:
# import and preprocess X_test images in correct order...
# ...for leaderboard prediction submissions
filenumbers = [str(x) for x in range(1, 5001)]
filenames = ["competition_data/testdata/test/test"+x for x in filenumbers]

# preprocess rbg images into 120,120,3 numpy ndarray
preprocessed_image_data = []
for i in filenames:
    try:
        preprocessed_image_data.append(preprocessor(i))
    except Exception as e :
        print(e)
        pass

In [39]:
preprocessed_image_data

[array([[[[ 332. ,  464. ,  239. , ..., 1325.5, 3332.5, 1728. ],
          [ 463. ,  596. ,  301. , ..., 1325.5, 3354. , 1728. ],
          [ 587. ,  650. ,  346. , ..., 1603.5, 3233.5, 1728. ],
          ...,
          [ 909. ,  724. ,  521. , ..., 2396.5, 2234. , 1558. ],
          [ 850. ,  724. ,  513. , ..., 2049. , 2015.5, 1558. ],
          [ 718. ,  609. ,  445. , ..., 2049. , 1926. , 1558. ]],
 
         [[ 317. ,  468. ,  231. , ..., 1325.5, 3251. , 1728. ],
          [ 401. ,  527. ,  258. , ..., 1325.5, 3295. , 1728. ],
          [ 406. ,  530. ,  256. , ..., 1603.5, 3400. , 1728. ],
          ...,
          [1079. ,  844. ,  601. , ..., 2396.5, 2316.5, 1558. ],
          [ 767. ,  615. ,  393. , ..., 2049. , 2036. , 1558. ],
          [ 631. ,  556. ,  336. , ..., 2049. , 1999.5, 1558. ]],
 
         [[ 285. ,  428. ,  203. , ..., 1240.5, 3456. , 1728. ],
          [ 351. ,  482. ,  213. , ..., 1240.5, 3408. , 1728. ],
          [ 452. ,  524. ,  256. , ..., 1454.5, 3148.5

In [40]:
len(preprocessed_image_data)

5000

In [53]:
X_test=np.vstack(preprocessed_image_data) 


In [54]:
X_test.shape

(5000, 120, 120, 7)

In [44]:
def divide_TestchannelbyMax(X_test,max_ValueArray):
    for i in range(6): 
        X_test[:,:,:,i] = (X_test[:,:,:,i]*255)/max_ValueArray[i]
    return X_test

X_test = divide_TestchannelbyMax(X_test,max_ValueArray)

In [45]:
#Set credentials using modelshare.org username/password

from aimodelshare.aws import set_credentials

# Note -- This is the unique rest api that powers this climate change image classification  Model Plaground
# ... Update the apiurl if submitting to a new competition

apiurl="https://srdmat3yhf.execute-api.us-east-1.amazonaws.com/prod/m"
set_credentials(apiurl=apiurl)

AI Modelshare Username:········
AI Modelshare Password:········
AI Model Share login credentials set successfully.


In [46]:
#Instantiate Competition

mycompetition= ai.Competition(apiurl)

In [55]:
#Submit Model 1: 

#-- Generate predicted y values (Model 1)
#Note: Keras predict returns the predicted column index location for classification models
prediction_column_index=model.predict(X_test).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [pandas.get_dummies(y_train).columns[i] for i in prediction_column_index]

157/157 [==============================] - 12s 78ms/step


In [56]:
np.save(f"Predictions_Model{model_number}",prediction_labels)

In [57]:
# Submit Model 1 to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels)

 16% [........                                            ]  2179072 / 12879139

 93% [................................................    ] 12050432 / 12879139

100% [....................................................] 12879139 / 12879139

/home/ecbm4040/climate_change/lib/python3.8/site-packages/aimodelshare/model.py:287: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  leaderboard = leaderboard.append(metadata, ignore_index=True, sort=False)
/home/ecbm4040/climate_change/lib/python3.8/site-packages/aimodelshare/model.py:289: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  leaderboard['username']=leaderboard.pop("username")
/home/ecbm4040/climate_change/lib/python3.8/site-packages/aimodelshare/model.py:290: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=

100% [........................................................] 775866 / 775866

/home/ecbm4040/climate_change/lib/python3.8/site-packages/aimodelshare/model.py:287: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  leaderboard = leaderboard.append(metadata, ignore_index=True, sort=False)


Insert search tags to help users find your model (optional): ResnetV2
Provide any useful notes about your model (optional): ResnetV2_7Channel

Your model has been submitted as model version 161

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:1535


In [58]:
# Get leaderboard to explore current best model architectures

# Get raw data in pandas data frame
data = mycompetition.get_leaderboard()

# Stylize leaderboard data
mycompetition.stylize_leaderboard(data)

In [60]:
data[data["username"] == "vkalmath"]

accuracy  f1_score  precision    recall ml_framework transfer_learning  \
1      0.7648  0.776539   0.791213  0.827111        keras               NaN   
22     0.7276  0.725968   0.722002  0.785111        keras               NaN   
30     0.6972  0.709685   0.722674  0.756667        keras               NaN   
33     0.6964  0.698332   0.749256  0.724222        keras               NaN   
64     0.6840  0.641584   0.727566  0.649778        keras              True   
65     0.6792  0.669706   0.672293  0.696000        keras               NaN   
68     0.6504  0.638267   0.715933  0.673333        keras               NaN   
77     0.6436  0.630026   0.718117  0.666000        keras               NaN   
160    0.3828  0.407672   0.461674  0.508222        keras               NaN   
173    0.3916  0.387116   0.427798  0.353556        keras               NaN   
186    0.1940  0.114698   0.069714  0.323333        keras               NaN   
188    0.2000  0.111111   0.066667  0.333333        keras               NaN   

    deep_learning  model_type  depth  num_params  ...  swish_act      loss  \
1            True  Sequential    8.0    136387.0  ...        NaN  function   
22           True  Sequential    7.0    136387.0  ...        NaN  function   
30           True  Sequential    7.0  20057603.0  ...        NaN       str   
33           True  Sequential    8.0   9573891.0  ...        NaN       str   
64           True  Sequential    7.0    136387.0  ...        NaN  function   
65           True  Sequential    8.0   9573891.0  ...        NaN       str   
68           True  Sequential   11.0   5288963.0  ...        NaN  function   
77           True  Sequential   11.0   5288963.0  ...        NaN  function   
160          True  Sequential    7.0   9573891.0  ...        NaN       str   
173          True  Sequential    8.0   1847811.0  ...        NaN       str   
186          True  Sequential    8.0   2102467.0  ...        NaN       str   
188          True  Sequential    8.0   2102467.0  ...        NaN       str   

     optimizer  memory_size  Member1  Member2  team  username  \
1         Adam    4813664.0      NaN      NaN   NaN  vkalmath   
22        Adam    4803824.0      NaN      NaN   NaN  vkalmath   
30         SGD   27253624.0      NaN      NaN   NaN  vkalmath   
33         SGD   14168312.0      NaN      NaN   NaN  vkalmath   
64        Adam    4803824.0      NaN      NaN   NaN  vkalmath   
65         SGD   14116664.0      NaN      NaN   NaN  vkalmath   
68        Adam    4938160.0      NaN      NaN   NaN  vkalmath   
77        Adam    4938160.0      NaN      NaN   NaN  vkalmath   
160        SGD   14105328.0      NaN      NaN   NaN  vkalmath   
173    RMSprop    2114800.0      NaN      NaN   NaN  vkalmath   
186       Adam   15819488.0      NaN      NaN   NaN  vkalmath   
188       Adam   15819488.0      NaN      NaN   NaN  vkalmath   

                      timestamp  version  
1    2022-03-19 19:11:33.485952       88  
22   2022-03-18 19:48:55.382639       73  
30   2022-03-24 03:19:52.050337      153  
33   2022-03-24 01:39:59.262445      152  
64   2022-03-17 22:32:37.060508       64  
65   2022-03-21 19:46:29.959795      120  
68   2022-03-19 23:06:22.545450       91  
77   2022-03-19 23:22:15.864357       92  
160  2022-03-23 20:42:09.766975      145  
173  2022-03-17 18:58:03.360045       59  
186  2022-03-24 16:27:46.431216      160  
188  2022-03-24 16:32:52.591178      161  

[12 rows x 54 columns]

## 5. Repeat submission process to improve place on leaderboard

*Train and submit your own models using code modeled after what you see above.*

It may also be useful to examine the architeture of models that perform particuarly well/poorly, or to compare models you've created with similar models submitted by others. Use the compare_models function in combination with the leaderboard to learn more about models that been previously submitted and potentially make decisiona about what you should do next.

In [ ]:
# Compare two or more models
data=mycompetition.compare_models([1, 5], verbose=1)
mycompetition.stylize_compare(data)